# PINN to solve lorentz equation

## Import NGSOLVE Mesh

In [1]:
from ngsolve import *
from ngsolve.webgui import Draw
from netgen.occ import *
from netgen.meshing import Mesh as NGMesh
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import plotly.graph_objects as go

import os 
# Import mesh and gridfunction from 4_MagVekPot_HomCoil.ipynb

i_c = 100
i_c_str = str(i_c)

filename_gfA = "gfA_homo_100_4ord.vec"
filename_mesh = "mesh_homo_100_4ord.vol"

# Load mesh
ngmesh = NGMesh()
ngmesh.Load(filename_mesh)
mesh = Mesh(ngmesh)

# Load Gridfunction and B
order = 2
V = HCurl(mesh, order=order - 1, nograds=True, dirichlet="outer")
gfA = GridFunction(V)
gfA.Load(filename_gfA)
B = curl(gfA)

# defining the magnetic field function to sample Bx By Bz from 

In [2]:
def magnetic_field(position):
    """
    Query the magnetic field for a given position.
    Return zero if position is out of the bounding box or index is invalid.

    Args:
        position (list or np.array): [x, y, z] position in space.
    Returns:
        np.array: [Bx, By, Bz] if in bounds and valid, otherwise [0, 0, 0].
    """
    # Check if position is inside the bounding box
    x, y, z = position

    try:
        if mesh.Contains(x, y, z):
            return np.array(B(mesh(x, y, z)))
        else:
            return np.array([0.0, 0.0, 0.0])

    except Exception as e:
        print(f"Error querying position {position}: {e}")
        return np.array([0.0, 0.0, 0.0])

print(magnetic_field([0,0,0]))

[-5.02835428e-04 -1.72476080e-04 -2.79104797e-01]


In [2]:
# Define the PINN Architecture

In [3]:
import torch
import random
import torch.nn as nn
m = 9.109383713928e-31  # electron mass in kg
q = -1.602176634e-19  # electron charge in Coulombs (or +ve if you want a proton)
# Remove fixed seed
random.seed(None)
np.random.seed(None)
torch.manual_seed(torch.seed())

class TrajectoryPINN(nn.Module):
    """
    Physics-Informed Neural Network (PINN) for predicting the trajectory of a charged particle.
    This network is designed to take a single time input and predict the spatial coordinates
    (x, y, z) of the particle at that time.
    """

    def __init__(self):
        """
        Initialize the neural network structure.
        The network consists of a series of fully connected (linear) layers with Tanh activation functions.
        """
        super().__init__()  # Call the parent class (nn.Module) constructor

        # Define the network architecture using nn.Sequential.
        # The architecture includes:
        # - An input layer that takes a single value (time t)
        # - Three hidden layers with 128 neurons each and Tanh activation functions
        # - An output layer with 3 neurons, representing the x(t), y(t), and z(t) coordinates
        self.net = nn.Sequential(
            nn.Linear(
                1, 128
            ),  # Input layer: maps 1 input (time t) to 128 hidden neurons
            nn.LeakyReLU(
                negative_slope=0.01
            ),  # Activation function: Tanh introduces non-linearity
            nn.Linear(
                128, 128
            ),  # Hidden layer: maps 128 neurons to another 128 neurons
            nn.LeakyReLU(negative_slope=0.01),  # Activation function: Tanh
           # nn.Linear(128, 128),  # Another hidden layer with 128 neurons
            #nn.LeakyReLU(negative_slope=0.01),  # Activation function: Tanh
            nn.Linear(128, 3),  # Output layer: maps 128 neurons to 3 outputs (x, y, z)
        )
        # Apply weight initialization
        self._initialize_weights()

    def _initialize_weights(self):
        for m in self.modules():
            if isinstance(m, nn.Linear):
                torch.nn.init.xavier_uniform_(m.weight)  # Xavier initialization
                if m.bias is not None:
                    torch.nn.init.zeros_(m.bias)  # Optional: Initialize biases to zero

    def forward(self, t):
        """
        Perform the forward pass of the network.

        Args:
            t (Tensor): A tensor containing the time input(s) for which to predict the trajectory.
                        Shape: (batch_size, 1), where each row is a single time value.

        Returns:
            Tensor: A tensor containing the predicted (x, y, z) coordinates for the input times.
                    Shape: (batch_size, 3), where each row represents [x(t), y(t), z(t)].
        """
        return self.net(t)  # Pass the input t through the network and return the output

# define the loss function

In [4]:
def clamp_position(pos_np, mins, maxs):
    # Replace NaNs with 0.0 (or something reasonable).
    # Otherwise, np.clip with NaNs will just return NaNs.
    pos_np = np.nan_to_num(pos_np, nan=0.0)
    # Now clip
    pos_np = np.clip(pos_np, mins, maxs)
    return pos_np


def physics_loss(model, t, s0, v0, device,display = False):
    """
    Compute the loss function for the PINN using the Lorentz force equation.
    Args:
        model (nn.Module): The PINN model.
        t (torch.Tensor): Time values, shape: (N, 1).
        s0 (torch.Tensor): Initial position [x0, y0, z0].
        v0 (torch.Tensor): Initial velocity [vx0, vy0, vz0].
        device (torch.device): Device (CPU or GPU).
    Returns:
        torch.Tensor: The total loss value.
    """
    # Enable autograd for time
    t.requires_grad = True

    # Predicted positions, shape: (N, 3)
    s = model(t)

    # Check shape of s
    if s.shape[1] != 3:
        raise ValueError(f"Expected model output to have shape (N, 3), got {s.shape}")

    # ------------------------------------------------------------------
    # Compute velocity v = ds/dt by taking partial derivatives of each
    # dimension of s w.r.t. t individually, then stacking them.
    # ------------------------------------------------------------------
    v_components = []
    for i in range(3):
        # s[:, i] has shape (N,)
        # We'll compute d(s[:, i]) / dt => shape (N,)
        grad_i = torch.autograd.grad(
            s[:, i],  # outputs
            t,  # inputs
            grad_outputs=torch.ones_like(s[:, i]),
            create_graph=True,
        )[
            0
        ]  # shape: (N, 1)

        v_components.append(grad_i.reshape(-1))  # make it (N,)

    # Stack into (N, 3)
    v = torch.stack(v_components, dim=1)
    # Debugging: Check velocity shape
    if v.shape[1] != 3:
        raise ValueError(f"Expected velocity to have shape (N, 3), got {v.shape}")

    # ------------------------------------------------------------------
    # Compute acceleration a = dv/dt similarly.
    # ------------------------------------------------------------------
    a_components = []
    for i in range(3):
        grad_i = torch.autograd.grad(
            v[:, i], t, grad_outputs=torch.ones_like(v[:, i]), create_graph=True
        )[0]

        a_components.append(grad_i.reshape(-1))

    a = torch.stack(a_components, dim=1)
    # Debugging: Check acceleration shape
    if a.shape[1] != 3:
        raise ValueError(f"Expected acceleration to have shape (N, 3), got {a.shape}")

    # Query magnetic field at predicted positions
    B_values = []
    for pos in s:
        # Convert the PyTorch tensor to a NumPy array.
        pos_np = pos.cpu().detach().numpy()
        # Clamp (and fix NaNs if any).
        pos_np_clamped = clamp_position(pos_np, mins=[-0.05, -0.05, -0.05],
                                           maxs=[ 0.05,  0.05,  0.05])
        # Now safely query the magnetic field.
        B_val = magnetic_field(pos_np_clamped)
        # Convert the result back to a PyTorch tensor on the same device.
        B_values.append(torch.tensor(B_val, dtype=torch.float32))

# Finally, stack them into a single tensor.
    B_values = torch.stack(B_values).to(device)  # Shape: (N, 3)
    # print(B_values)
    # Debugging: Check B_values shape
    if B_values.shape[1] != 3:
        raise ValueError(
            f"Expected B_values to have shape (N, 3), got {B_values.shape}"
        )

    # Lorentz force residual
    lorentz_residual = m * a - q * torch.cross(v, B_values, dim=1)
    physics_loss_val = torch.mean(lorentz_residual**2)

    # Initial conditions loss
    ic_loss = torch.mean((s[0] - s0) ** 2) + torch.mean((v[0] - v0) ** 2)

    # Dynamic weighting
    # Dynamic weighting using softmax
    total_loss = physics_loss_val + ic_loss
    physics_weight = total_loss / (2 * (physics_loss_val + 1e-8))
    ic_weight = total_loss / (2 * (ic_loss + 1e-8))

    # Calculate final weighted loss
    weighted_loss = physics_weight * physics_loss_val + ic_weight * ic_loss

    if display:
        print(
            f"Physics loss: {physics_loss_val.item()}, Physics weight: {physics_weight.item()}, Weighted Physics loss: {physics_weight.item() * physics_loss_val.item()}"
        )
        print(
            f"IC loss: {ic_loss.item()}, IC weight: {ic_weight.item()}, Weighted IC loss: {ic_weight.item() * ic_loss.item()}"
        )

    return weighted_loss

# definition of the training loop

You can switch on or off different types of Optimizers with different learning rates by commenting out or in the break statement after each for loop
You can further train an existing model by simply loading it before the training loop be aware that you have to adapt the code slightly in order to do so. If doubt persists, chatgpt can easly solve this for you

In [59]:
import torch
from torch.optim.lr_scheduler import ReduceLROnPlateau

loss_history_hybrid = []
def train_hybrid_odol():
    """
    Hybrid training loop that:
      1) Runs 1 epoch with Adam
      2) Runs 1 epoch with LBFGS
    Uses the existing TrajectoryPINN() model and physics_loss() function.
    """
    # Choose device
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

    # Instantiate your existing model
    model = TrajectoryPINN().to(device)

    # Define initial conditions (example)
    s0 = torch.tensor([[0.0, 0.007, -0.05]], device=device)
    v0 = torch.tensor([[0.0, 0.0, 121379551.046]], device=device)  # 118250656

    # Time domain for training
    t_train = torch.linspace(0, 1e-5, 1000, device=device).unsqueeze(1)

    # -----------------------------------------------------------
    # Part 1: Train with Adam for 1 epoch
    # -----------------------------------------------------------
    adam_optimizer = torch.optim.Adam(model.parameters(), lr=1e-1)
    print("Starting 1 epoch with Adam...")

    for epoch in range(20500):
        break
        
        adam_optimizer.zero_grad()
        loss = physics_loss(model, t_train, s0, v0, device, display=False)
        loss.backward()
        loss_history_hybrid.append(loss.item())
        adam_optimizer.step()
        print(f"[Adam 1]Epoch: {epoch} Loss: {loss.item()} ")
        if loss.item() < 4e4:#7
            break
    # -----------------------------------------------------------
    # Part 1.1: Train with Adam for 1 epoch
    # -----------------------------------------------------------
    adam_optimizer = torch.optim.Adam(model.parameters(), lr=1e-2)
    print("Starting 1 epoch with Adam...")

    for epoch in range(20500):
        break
        adam_optimizer.zero_grad()
        loss = physics_loss(model, t_train, s0, v0, device, display=False)
        loss.backward()
        loss_history_hybrid.append(loss.item())
        adam_optimizer.step()
        print(f"[Adam 1.1]Epoch: {epoch} Loss: {loss.item()} ")
        if loss.item() < 8e4:
            break
        # -----------------------------------------------------------
    # Part 1.2: Train with Adam for 1 epoch
    # -----------------------------------------------------------
    adam_optimizer = torch.optim.Adam(model.parameters(), lr=1.5e-3)
    print("Starting 1 epoch with Adam...")

    for epoch in range(20500):
        break
        adam_optimizer.zero_grad()
        loss = physics_loss(model, t_train, s0, v0, device, display=False)
        loss.backward()
        loss_history_hybrid.append(loss.item())
        adam_optimizer.step()
        print(f"[Adam 1.2]Epoch: {epoch} Loss: {loss.item()} ")
        if loss.item() < 2e2:#e3
            break
    # -----------------------------------------------------------
    # Part 1.5: Train with Adam for 1 epoch
    # -----------------------------------------------------------
    adam_optimizer = torch.optim.Adam(model.parameters(), lr=1e-1) #1e-3

    print("Starting 1.5 epoch with Adam...")
    scheduler = ReduceLROnPlateau(
        adam_optimizer, mode="min", factor=0.99, patience=30, verbose=True,min_lr=1e-7, threshold=0.00001, threshold_mode="abs",cooldown=10
    )

    for epoch in range(50000):
        
        adam_optimizer.zero_grad()
        loss = physics_loss(model, t_train, s0, v0, device, display=False)
        loss.backward()
        loss_history_hybrid.append(loss.item())
        adam_optimizer.step()
        scheduler.step(loss)
        current_lr = adam_optimizer.param_groups[0]["lr"]

        print(f"[Adam 1.5] Epoch: {epoch}, Loss: {loss.item()}, LR: {current_lr}")
        if loss.item() < 1e-13:
            break

        # -----------------------------------------------------------
        # Part 1.5: Train with Adrmspr am for 1 epoch
        # -----------------------------------------------------------
    rmsprop_optimizer = torch.optim.RMSprop(model.parameters(), lr=1e-1, alpha=0.99)

    print("Starting 1.5 epoch with RMSprop...")
    scheduler = ReduceLROnPlateau(
    rmsprop_optimizer,
    mode="min",
    factor=0.99,
    patience=100,
    verbose=True,
    min_lr=1e-7,
    threshold=0.00001,
    threshold_mode="abs",
    cooldown=10,
    )

    for epoch in range(50000):
        break
        rmsprop_optimizer.zero_grad()
        loss = physics_loss(model, t_train, s0, v0, device, display=False)
        loss.backward()
        loss_history_hybrid.append(loss.item())
        rmsprop_optimizer.step()
        scheduler.step(loss)
        current_lr = rmsprop_optimizer.param_groups[0]["lr"]

        print(f"[RMSprop 1.5] Epoch: {epoch}, Loss: {loss.item()}, LR: {current_lr}")
        if loss.item() < 1e-13:
            break

        # -----------------------------------------------------------
    # Part 2: Train with adamw for 1 epoch
    # -----------------------------------------------------------
    adamw_optimizer = torch.optim.AdamW(
        model.parameters(), lr=1e-1, weight_decay=1.2e-3
    )  # Add weight_decay for regularization

    print("Starting 1.5 epoch with AdamW...")
    scheduler = ReduceLROnPlateau(
    adamw_optimizer,
    mode="min",
    factor=0.99,
    patience=40,
    verbose=True,
    min_lr=1e-7,
    threshold=0.00001,
    threshold_mode="abs",
    cooldown=10,
    )

    for epoch in range(50000):
       # break
        adamw_optimizer.zero_grad()
        loss = physics_loss(model, t_train, s0, v0, device, display=False)
        loss.backward()
        loss_history_hybrid.append(loss.item())
        adamw_optimizer.step()
        scheduler.step(loss)
        current_lr = adamw_optimizer.param_groups[0]["lr"]

        print(f"[AdamW 1.5] Epoch: {epoch}, Loss: {loss.item()}, LR: {current_lr}")
        if loss.item() < 1e-13:
            break
    # -----------------------------------------------------------
    # Part 2: Train with adamdelta for 1 epoch
    # -----------------------------------------------------------
    adadelta_optimizer = torch.optim.Adadelta(model.parameters(), lr=0.01, rho=0.9)

    print("Starting 1.5 epoch with Adadelta...")
    scheduler = ReduceLROnPlateau(
        adadelta_optimizer,
        mode="min",
        factor=0.99,
        patience=30,
        verbose=True,
        min_lr=1e-7,
        threshold=0.00001,
        threshold_mode="abs",
        cooldown=10,
    )

    for epoch in range(50000):
        break
        adadelta_optimizer.zero_grad()
        loss = physics_loss(model, t_train, s0, v0, device, display=False)
        loss.backward()
        loss_history_hybrid.append(loss.item())
        adadelta_optimizer.step()
        scheduler.step(loss)
        current_lr = adadelta_optimizer.param_groups[0]["lr"]

        print(f"[Adadelta 1.5] Epoch: {epoch}, Loss: {loss.item()}, LR: {current_lr}")
        if loss.item() < 1e-13:
            break

    # -----------------------------------------------------------
    # Part 2: Train with LBFGS for 1 epoch
    # -----------------------------------------------------------
    lbfgs_optimizer = torch.optim.LBFGS(
        model.parameters(),
        lr=1.221e-4,
        max_iter=50000,
        tolerance_grad=1e-9,
        tolerance_change=1e-9,
        history_size=100,
    )
    print("Starting 1 epoch with LBFGS...")

    # We will define a closure for LBFGS
    def closure():
        lbfgs_optimizer.zero_grad()
        # For display, set it to False by default
        # We'll override it in the main loop if needed
        loss = physics_loss(model, t_train, s0, v0, device, display=False)
        loss.backward()
        # Gradient clipping, if desired
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=10.0)
        if torch.isnan(loss):
            print("Loss is NaN! Stopping LBFGS step.")
            # Either return a large dummy loss or raise an error
            return torch.tensor(1e20, requires_grad=True)
        return loss

    for epoch in range(5000):
        break
        lbfgs_loss = lbfgs_optimizer.step(closure)
        print(f"[LBFGS]Epoch: {epoch} Loss: {lbfgs_loss}")
        loss_history_hybrid.append(lbfgs_loss.item())

        if lbfgs_loss.item() < 1e-5:
            break
    # Optionally save the final model
    torch.save(model.state_dict(), "trajectory_pinn_hybrid_odol_v4.pth")
    print("Hybrid training (1 epoch Adam + 1 epoch LBFGS) complete.")

    return model
train_hybrid_odol()

Starting 1 epoch with Adam...
Starting 1 epoch with Adam...
Starting 1 epoch with Adam...
Starting 1.5 epoch with Adam...
[Adam 1.5] Epoch: 0, Loss: 2455499106680832.0, LR: 0.1
[Adam 1.5] Epoch: 1, Loss: 2455499106680832.0, LR: 0.1
[Adam 1.5] Epoch: 2, Loss: 2455498301374464.0, LR: 0.1
[Adam 1.5] Epoch: 3, Loss: 2455496690761728.0, LR: 0.1
[Adam 1.5] Epoch: 4, Loss: 2455495885455360.0, LR: 0.1
[Adam 1.5] Epoch: 5, Loss: 2455496422326272.0, LR: 0.1
[Adam 1.5] Epoch: 6, Loss: 2455497496068096.0, LR: 0.1
[Adam 1.5] Epoch: 7, Loss: 2455493201100800.0, LR: 0.1
[Adam 1.5] Epoch: 8, Loss: 2455496422326272.0, LR: 0.1
[Adam 1.5] Epoch: 9, Loss: 2455478168715264.0, LR: 0.1
[Adam 1.5] Epoch: 10, Loss: 2455454277959680.0, LR: 0.1
[Adam 1.5] Epoch: 11, Loss: 2455441393057792.0, LR: 0.1
[Adam 1.5] Epoch: 12, Loss: 2455431997816832.0, LR: 0.1
[Adam 1.5] Epoch: 13, Loss: 2455493469536256.0, LR: 0.1
[Adam 1.5] Epoch: 14, Loss: 2455394685288448.0, LR: 0.1
[Adam 1.5] Epoch: 15, Loss: 2455485953343488.0, 

TrajectoryPINN(
  (net): Sequential(
    (0): Linear(in_features=1, out_features=128, bias=True)
    (1): LeakyReLU(negative_slope=0.01)
    (2): Linear(in_features=128, out_features=128, bias=True)
    (3): LeakyReLU(negative_slope=0.01)
    (4): Linear(in_features=128, out_features=3, bias=True)
  )
)

# display the loss curve

In [ ]:
# Plot the loss curve
import matplotlib.pyplot as plt

plt.plot(loss_history_hybrid)
plt.xlabel("Epoch")
plt.ylabel("Loss")
plt.yscale("log")  # Set y-axis to logarithmic scale


plt.title("Training Loss Curve")
plt.grid()
plt.show()
v3

# create trajectory predictions

In [5]:
import plotly.graph_objects as go
import torch
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Load the trained model
model = TrajectoryPINN().to(device)
model.load_state_dict(
    torch.load("trajectory_pinn_hybrid_odol_v4_prepreretrained.pth")
)
model.eval()

# Generate predictions
t_test = torch.linspace(0, 1e-5, 1000, device=device).unsqueeze(1)  # Time values
with torch.no_grad():
    s_pred = model(t_test).cpu().numpy()  # Predicted positions

# Extract coordinates
x_pred, y_pred, z_pred = s_pred[:, 0], s_pred[:, 1], s_pred[:, 2]

# Create interactive 3D plot
fig = go.Figure()

fig.add_trace(
    go.Scatter3d(
        x=x_pred,
        y=y_pred,
        z=z_pred,
        mode="lines",
        line=dict(color="blue", width=2),
        name="Predicted Trajectory",
    )
)

# Add titles and labels
fig.update_layout(
    title="Predicted 3D Trajectory of the Particle",
    scene=dict(xaxis_title="X", yaxis_title="Y", zaxis_title="Z"),
)

# Show the plot
fig.show()